In [8]:
import pandas as pd
import numpy as np
import os
import time
import random
import gensim
import numpy as np
import os
import torch
from gensim.models import KeyedVectors
from matplotlib import pyplot as plt
from matplotlib.pyplot import figure

/home/fatma/.local/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
def get_mean_vector(model, words):
    # remove out-of-vocabulary words
    # words: target list words
    # returns average vector for all words in target list
    import numpy as np
    words = [word for word in words if word in model.index_to_key]
    if len(words) >= 1:
        return np.mean(model[words], axis=0)
    else:
        return []

def get_similarity_Scores(v1,v2):
    from numpy import dot
    from numpy.linalg import norm
    return dot(v1,v2)/(norm(v1)*norm(v2))

def normalize_data(a):
    normalizded_a = []
    amin, amax = min(a), max(a)
    for i in a:
        normalizded_a.append((i-amin) / (amax-amin))
    return normalizded_a
    
def get_similarity_scores_between_target_words_and_attribute_words(model, attribute_words, target_words):
    
    similarity_scores_summary = {}
    words = []
    mean_sim_socres = []

    target_words = [word for word in target_words if word in model.index_to_key]
    attribute_words = [word for word in attribute_words if word in model.index_to_key]
    
    if len(target_words) >= 1 and len(attribute_words) >=1:
        for i in target_words:
            similarity_scores = []
            words.append(i)
            for j in attribute_words:
                cos_sim = get_similarity_Scores(model[i], model[j])
                similarity_scores.append(cos_sim)
            mean_sim_socres.append(np.mean(normalize_data(similarity_scores)))

    similarity_scores_summary["word"] = words
    similarity_scores_summary["mean_sim_score"] = mean_sim_socres
    return similarity_scores_summary

def get_similarity_scores_between_avergare_target_vector_and_attribute_words(model, att_words, target_vector):
    # remove out-of-vocabulary words
    # att_words: wors in the attribute list
    # target_vector: average vector of all words in target group
    similarity_scores_summary = {}
    words_list = []
    similarity_scores = []
    words = [word for word in att_words if word in model.index_to_key]
    print(len(words))
    if len(words) >= 1:
        for i in words:
            print(i)
            words_list.append(i)
            cos_sim = get_similarity_Scores(model[i], target_vector)
            similarity_scores.append(cos_sim)
    similarity_scores_summary["words"] = words_list
    similarity_scores_summary["cos_sim_scores"] = similarity_scores
    similarity_scores_summary["sim_score"] = normalize_data(similarity_scores)

    return similarity_scores_summary


## Read profane words

In [9]:
data_folder = "../../Data/"
embeddings_folder = data_folder+"/word embeddings/"
results_folder = "Results/ethnicity_similarities/UD/"

In [10]:
profane_words = open(data_folder+"swear_words.txt").read().splitlines()

## read word embeddings

In [11]:
def get_google_news_embeddings(filename,binary=False):
    w2v_model = gensim.models.KeyedVectors.load_word2vec_format(filename, binary=binary)
    return w2v_model


## word similarity

In [6]:
# convert text to w2v
#from gensim.scripts.glove2word2vec import glove2word2vec
#GLOVE_DIR = data_folder+"/glove.6B.300d_WP.txt"
#w2v_file = data_folder+"/wv_2_glove.6B.300d_WP.txt"
#glove2word2vec(GLOVE_DIR, w2v_file)

In [12]:
model = get_google_news_embeddings(embeddings_folder+"ud_embeddings/ud_basic.vec")

## similar words

In [20]:
model.most_similar("girl")

[('she', 0.7682197093963623),
 ('guy', 0.7594241499900818),
 ('boy', 0.7163589596748352),
 ('person', 0.6964590549468994),
 ('girls', 0.6933688521385193),
 ('her', 0.6848600506782532),
 ('chick', 0.6718631982803345),
 ('man', 0.6467651128768921),
 ('woman', 0.6433965563774109),
 ('vaiga', 0.6354042887687683)]

In [14]:
model.most_similar("queer")

[('fag', 0.7341068983078003),
 ('homo', 0.7097572088241577),
 ('homosexual', 0.6834489703178406),
 ('bumblaster', 0.6723655462265015),
 ('buttyman', 0.6675945520401001),
 ('quuer', 0.6672463417053223),
 ('faggot', 0.6661654710769653),
 ('poufter', 0.6657533049583435),
 ('spydurgot', 0.6627064347267151),
 ('gay', 0.6618685722351074)]

In [15]:
model.most_similar("queers")

[('fags', 0.6889349222183228),
 ('faggots', 0.6695451140403748),
 ('homos', 0.6086224317550659),
 ('gays', 0.59735107421875),
 ('doushes', 0.5904637575149536),
 ('homosexuals', 0.5880358815193176),
 ('queer', 0.5694150924682617),
 ('bagbars', 0.5664904713630676),
 ('gaywads', 0.565146803855896),
 ('fagbags', 0.5409811735153198)]

In [25]:
model.most_similar("immigrant")

[('immigrants', 0.7126596570014954),
 ('criminalien', 0.617576003074646),
 ('mexiscum', 0.6108182072639465),
 ('immigration', 0.5993794202804565),
 ('venesday', 0.5911235809326172),
 ('scratchback', 0.5898543000221252),
 ('sandbaby', 0.5847991704940796),
 ('spickbitch', 0.5846492648124695),
 ('trespacito', 0.5819947123527527),
 ('illiegal', 0.5684493184089661)]

## minority and majority words

In [8]:
harmless_majority_words_clean = ["hetrosexual", "cisgender", "man","male","boy","son","father","husband","brother","white","caucasian",
                                 "european american","european", "norwegian", "canadian", "german", "australian", "english",
                                "french", "american", "swedish", "dutch"]

target_words = ["lesbian","gay","bisexual","transgender","tran","queer",
                "lgbt","lgbtq","homosexual", "woman", "female", "girl","wife","sister","daughter","mother", "non-binary",
               "african", "african american", "asian", "black", "hispanic", "latin", "mexican", "indian", "middle eastern",
                "arab"]

words = harmless_majority_words_clean + target_words

In [9]:
profane_vector = get_mean_vector(model, profane_words)
vec_majority_sim_dict = get_similarity_scores_between_avergare_target_vector_and_attribute_words(model, words, profane_vector)
pd.DataFrame(vec_majority_sim_dict).to_csv(results_folder+"_minority_and_majority_words_sim_to_profane_vector.csv")

46
hetrosexual
cisgender
man
male
boy
son
father
husband
brother
white
caucasian
european
norwegian
canadian
german
australian
english
french
american
swedish
dutch
lesbian
gay
bisexual
transgender
tran
queer
lgbt
lgbtq
homosexual
woman
female
girl
wife
sister
daughter
mother
non-binary
african
asian
black
hispanic
latin
mexican
indian
arab


In [10]:
figure(figsize=(25, 10), dpi=1200)
sorted_index = np.argsort(vec_majority_sim_dict["sim_score"])

x_axis = np.arange(len(vec_majority_sim_dict["words"]))
y_axis = [vec_majority_sim_dict["sim_score"][i] for i in sorted_index]
x_ticks = [vec_majority_sim_dict["words"][i] for i in sorted_index]
plt.bar(x_axis, y_axis)
plt.xticks(x_axis, x_ticks, fontsize=40, fontweight='bold', rotation=90)
plt.ylabel("similarity score", fontsize=40, fontweight='bold')
plt.yticks(np.arange(0.1,1.1,0.1),fontsize=40, fontweight='bold')
plt.savefig(results_folder+"similarity_score_of_minority_and_majority_words_to_profanity_vector.pdf", bbox_inches='tight')